# Reshaping DataFrames

In [1]:
using DataFrames

## Wide to long

In [2]:
x = DataFrame(id=[1, 2, 3, 4], id2=[1, 1, 2, 2], M1=[11, 12, 13, 14], M2=[111, 112, 113, 114])

4×4 DataFrame
 Row │ id     id2    M1     M2    
     │ Int64  Int64  Int64  Int64 
─────┼────────────────────────────
   1 │     1      1     11    111
   2 │     2      1     12    112
   3 │     3      2     13    113
   4 │     4      2     14    114

first pass measure variables and then id-variable

In [3]:
stack(x, [:M1, :M2], :id)

8×3 DataFrame
 Row │ id     variable  value 
     │ Int64  String    Int64 
─────┼────────────────────────
   1 │     1  M1           11
   2 │     2  M1           12
   3 │     3  M1           13
   4 │     4  M1           14
   5 │     1  M2          111
   6 │     2  M2          112
   7 │     3  M2          113
   8 │     4  M2          114

add `view=true` keyword argument to make a view; in that case columns of the resulting data frame share memory with columns of the source data frame, so the operation is potentially unsafe.
Optionally, you can rename columns.

In [4]:
stack(x, ["M1", "M2"], "id", variable_name="key", value_name="observed")

8×3 DataFrame
 Row │ id     key     observed 
     │ Int64  String  Int64    
─────┼─────────────────────────
   1 │     1  M1            11
   2 │     2  M1            12
   3 │     3  M1            13
   4 │     4  M1            14
   5 │     1  M2           111
   6 │     2  M2           112
   7 │     3  M2           113
   8 │     4  M2           114

if second argument is omitted in `stack` , all other columns are assumed to be the id-variables

In [5]:
stack(x, Not([:id, :id2]))

8×4 DataFrame
 Row │ id     id2    variable  value 
     │ Int64  Int64  String    Int64 
─────┼───────────────────────────────
   1 │     1      1  M1           11
   2 │     2      1  M1           12
   3 │     3      2  M1           13
   4 │     4      2  M1           14
   5 │     1      1  M2          111
   6 │     2      1  M2          112
   7 │     3      2  M2          113
   8 │     4      2  M2          114

you can use index instead of symbol

In [6]:
stack(x, Not([1, 2]))

8×4 DataFrame
 Row │ id     id2    variable  value 
     │ Int64  Int64  String    Int64 
─────┼───────────────────────────────
   1 │     1      1  M1           11
   2 │     2      1  M1           12
   3 │     3      2  M1           13
   4 │     4      2  M1           14
   5 │     1      1  M2          111
   6 │     2      1  M2          112
   7 │     3      2  M2          113
   8 │     4      2  M2          114

if `stack` is not passed any measure variables by default numeric variables are selected as measures

In [7]:
x = DataFrame(id=[1, 1, 1], id2=['a', 'b', 'c'], a1=rand(3), a2=rand(3))
stack(x)

6×4 DataFrame
 Row │ id     id2   variable  value     
     │ Int64  Char  String    Float64   
─────┼──────────────────────────────────
   1 │     1  a     a1        0.645389
   2 │     1  b     a1        0.0893361
   3 │     1  c     a1        0.140096
   4 │     1  a     a2        0.241577
   5 │     1  b     a2        0.0454197
   6 │     1  c     a2        0.879643

here all columns are treated as measures:

In [8]:
stack(DataFrame(rand(3, 2), :auto))

6×2 DataFrame
 Row │ variable  value    
     │ String    Float64  
─────┼────────────────────
   1 │ x1        0.117252
   2 │ x1        0.347188
   3 │ x1        0.821351
   4 │ x2        0.694786
   5 │ x2        0.686708
   6 │ x2        0.1938

duplicates in key are silently accepted

In [9]:
df = DataFrame(rand(3, 2), :auto)
df.key = [1, 1, 1]
mdf = stack(df)

6×3 DataFrame
 Row │ key    variable  value     
     │ Int64  String    Float64   
─────┼────────────────────────────
   1 │     1  x1        0.793118
   2 │     1  x1        0.0725136
   3 │     1  x1        0.546648
   4 │     1  x2        0.938334
   5 │     1  x2        0.727929
   6 │     1  x2        0.603351

## Long to wide

In [10]:
x = DataFrame(id=[1, 1, 1], id2=['a', 'b', 'c'], a1=rand(3), a2=rand(3))

3×4 DataFrame
 Row │ id     id2   a1        a2       
     │ Int64  Char  Float64   Float64  
─────┼─────────────────────────────────
   1 │     1  a     0.579926  0.457018
   2 │     1  b     0.820986  0.797507
   3 │     1  c     0.202164  0.67697

In [11]:
y = stack(x)

6×4 DataFrame
 Row │ id     id2   variable  value    
     │ Int64  Char  String    Float64  
─────┼─────────────────────────────────
   1 │     1  a     a1        0.579926
   2 │     1  b     a1        0.820986
   3 │     1  c     a1        0.202164
   4 │     1  a     a2        0.457018
   5 │     1  b     a2        0.797507
   6 │     1  c     a2        0.67697

standard unstack with a specified key

In [12]:
unstack(y, :id2, :variable, :value)

3×3 DataFrame
 Row │ id2   a1        a2       
     │ Char  Float64?  Float64? 
─────┼──────────────────────────
   1 │ a     0.579926  0.457018
   2 │ b     0.820986  0.797507
   3 │ c     0.202164  0.67697

all other columns are treated as keys

In [13]:
unstack(y, :variable, :value)

3×4 DataFrame
 Row │ id     id2   a1        a2       
     │ Int64  Char  Float64?  Float64? 
─────┼─────────────────────────────────
   1 │     1  a     0.579926  0.457018
   2 │     1  b     0.820986  0.797507
   3 │     1  c     0.202164  0.67697

all columns other than named :variable and :value are treated as keys

In [14]:
unstack(y)

3×4 DataFrame
 Row │ id     id2   a1        a2       
     │ Int64  Char  Float64?  Float64? 
─────┼─────────────────────────────────
   1 │     1  a     0.579926  0.457018
   2 │     1  b     0.820986  0.797507
   3 │     1  c     0.202164  0.67697

you can rename the unstacked columns

In [15]:
unstack(y, renamecols=n -> string("unstacked_", n))

3×4 DataFrame
 Row │ id     id2   unstacked_a1  unstacked_a2 
     │ Int64  Char  Float64?      Float64?     
─────┼─────────────────────────────────────────
   1 │     1  a         0.579926      0.457018
   2 │     1  b         0.820986      0.797507
   3 │     1  c         0.202164      0.67697

In [16]:
df = stack(DataFrame(rand(3, 2), :auto))

6×2 DataFrame
 Row │ variable  value     
     │ String    Float64   
─────┼─────────────────────
   1 │ x1        0.0932271
   2 │ x1        0.210632
   3 │ x1        0.461863
   4 │ x2        0.681666
   5 │ x2        0.104251
   6 │ x2        0.0205399

unable to unstack when no key column is present

In [17]:
try
    unstack(df, :variable, :value)
catch e
    show(e)
end

ArgumentError("Duplicate entries in unstack at row 2 for key () and variable x1. Pass `combine` keyword argument to specify how they should be handled.")

`unstack` fills missing combinations with `missing`, but you can change this default with `fill` keyword argument.

In [18]:
df = DataFrame(key=[1, 1, 2], variable=["a", "b", "a"], value=1:3)

3×3 DataFrame
 Row │ key    variable  value 
     │ Int64  String    Int64 
─────┼────────────────────────
   1 │     1  a             1
   2 │     1  b             2
   3 │     2  a             3

In [19]:
unstack(df, :variable, :value)

2×3 DataFrame
 Row │ key    a       b       
     │ Int64  Int64?  Int64?  
─────┼────────────────────────
   1 │     1       1        2
   2 │     2       3  missing 

In [20]:
unstack(df, :variable, :value, fill=0)

2×3 DataFrame
 Row │ key    a      b     
     │ Int64  Int64  Int64 
─────┼─────────────────────
   1 │     1      1      2
   2 │     2      3      0

---

*This notebook was generated using [Literate.jl](https://github.com/fredrikekre/Literate.jl).*